Ici on récupère les données via PISTE l'API permettant d'avoir accès aux données de Légifrance, le code de connexion OAuth est donné sur le Gitlab de Piste à cette [adresse](https://gitlab.com/piste_lab/oauth_connectors/-/blob/master/Python/Oauth2ClientCredentialsTest.py?ref_type=heads). Il est tout de même nécessaire d'installer les modules du code suivant.

# Code pour récupérer les données de Légifrance via l'API Piste


Ce notebook contient les différents codes qui nous ont permis d'accéder aux données disponibles grâce à l'API Piste de Légifrance.

Sur l'API de Légifrance les requêtes doivent être faites sur un fonds, soit un filtre correspondant à une catégorie spécifique de la base de données de Légifrance. Les différents fonds incluent notamment LODA , qui regroupe les lois, les ordonnances, les décrets et les arrêtés, mais il y a aussi CODE pour les documents relatifs aux différents codes et ALL qui permet de faire une requête sur tous les fonds. 

Au début de notre récupération des données nos requêtes ont été effectuées sur le fond LODA, ensuite CODE et enfin ALL, avant de revenir sur LODA. Cet ordre n'est dû qu'à l'absence de documentation claire, au faible nombre de projets présents sur internet utilisant l'API de Légifrance et d'erreurs que l'on n'arrive pas à expliquer et qui nous empêchent d'avoir accès à l'intégralité des fonds. 

En fait, lorsqu'on effectue une requête, l'API ne nous renvoie qu'un nombre limité de résultats (100 maximum), donc il faut faire une boucle pour récupérer tous les documents. Les requêtes supérieures au 10001e éléments renvoient une erreur 503, soit une erreur du serveur. Malgré des recherches et des mails envoyés au support et à des personnes travaillant à l'AIFE (Agence pour l'Informatique Financière de l'État) sur l'API de Légifrance nous n'avons pas trouvé de solution à cela. 

Ainsi, pour l'avancement du projet, nous avons pris la décision de ne récupérer que les données sur le fond LODA, car ce fond est d'après nous le plus pertinent - les modifications des codes étant plus difficiles à étudier sous l'angle quantitatif par rapport aux lois, car il s'agit en partie de modification de vocabulaire employé.

### Sommaire 

* [Installations des données sur le fond LODA](#section1)


### Récupération des données avec le fond LODA <a class="anchor" id="section1"></a>

In [3]:
%pip install python-dotenv
%pip install requests-oauthlib


Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


In [27]:
import os
from dotenv import load_dotenv
import requests
from requests_oauthlib import OAuth2Session
import requests
import pandas as pd
import math
import json
from datetime import datetime, timedelta
from threading import Thread
import zipfile
import numpy as np 
import re

In [5]:
API_HOST = "https://api.piste.gouv.fr/dila/legifrance/lf-engine-app"

In [6]:
def get_client():
    """
    Récupère un client OAuth2Session configuré avec un token d'accès depuis le serveur OAuth. 

    :return: Un objet OAuth2Session prêt à être utilisé pour des requêtes API.
    """
    TOKEN_URL = "https://oauth.piste.gouv.fr/api/oauth/token"

    # Charger les identifiants client depuis le fichier .env
    load_dotenv()
    client_id = os.getenv("CLIENT_ID")
    client_secret = os.getenv("CLIENT_SECRET")

    # Requête pour obtenir le token
    res = requests.post(
        TOKEN_URL,
        data={
            "grant_type": "client_credentials",
            "client_id": client_id,
            "client_secret": client_secret,
            "scope": "openid"
        }
    )

    res.raise_for_status()  # Lever une erreur si la requête échoue

    token = res.json()

    # Retourner un client OAuth2Session configuré
    return OAuth2Session(client_id, token=token)

In [7]:
def save_results_to_file(results, file_name, current_page):
    """
    Sauvegarde les résultats dans un fichier JSON. Si le fichier existe, ajoute les nouvelles données.

    :param results: Liste des résultats à sauvegarder.
    :param file_name: Nom du fichier JSON.
    :param current_page: La page actuelle traitée.
    """
    try:
        # Charger les données existantes si le fichier existe
        with open(file_name, "r", encoding="utf-8") as file:
            existing_data = json.load(file)
            if not isinstance(existing_data, dict):
                raise ValueError("Le fichier de sauvegarde n'est pas correctement structuré.")
            existing_results = existing_data.get("results", [])
            start_page = existing_data.get("current_page", 1)
    except (FileNotFoundError, ValueError):
        existing_results = []
        start_page = 1

    # Ajouter les nouveaux résultats
    existing_results.extend(results)

    # Sauvegarder les résultats mis à jour avec la page actuelle
    with open(file_name, "w", encoding="utf-8") as file:
        json.dump({"results": existing_results, "current_page": current_page}, file, ensure_ascii=False, indent=4)

In [8]:
def collect_all_results(api_host, code, file_name):
    ''' 
    Récupère tous les résultats relatifs à une requête API. 

    :param api_host: addresse à laquelle envoyer la requête avec le endpoint correspondant 
    :param code: code permettant de faire la requête correspondante à nos recherches, 
    pour l'utilisation de la fonction on mettra de fait 
    collect_all_results(api_host, json = code)
    
    :return: le nombre total de page 
    '''

    # Charger la page de démarrage depuis le fichier de sauvegarde s'il existe comme il faut 
    try:
        with open(file_name, "r", encoding="utf-8") as file:
            saved_data = json.load(file)
            if not isinstance(saved_data, dict):
                raise ValueError("Le fichier de sauvegarde n'est pas correctement structuré.")
            start_page = saved_data.get("current_page", 1)
    except (FileNotFoundError, ValueError):
        print(f"Fichier {file_name} introuvable ou mal structuré. Démarrage depuis la première page.")
        start_page = 1

    # Initialiser le client OAuth2Session 
    client = get_client()

    # On fixe un temps d'expiration à 55 min car le token dure 60 min
    expires_in = 55*60
    token_expiry = datetime.now() + timedelta(seconds=expires_in) 

    # Récupérer le total de résultats et calculer le nombre de pages
    response = client.post(api_host, json=code).json()
    total_results = response.get("totalResultNumber", 0)
    page_size = code["recherche"]["pageSize"]
    total_pages = math.ceil(total_results / page_size)

    print(f"Total de résultats : {total_results}")
    print(f"Nombre de pages à récupérer : {total_pages}")
    print(f"Reprise à partir de la page {start_page}")

    # Liste pour stocker les résultats courants
    all_results = []

    # On boucle sur le nombre de pages
    for page_number in range(start_page, total_pages + 1):

        # Vérifier si le token doit être renouvelé
        if datetime.now() >= token_expiry:
            print("Renouvellement du client OAuth...")
            client = get_client()
            token_expiry = datetime.now() + timedelta(seconds=expires_in)
        
        # Récupère le bon numéro de page et lance la requête
        print(f"Récupération de la page {page_number}/{total_pages}...")
        code["recherche"]["pageNumber"] = page_number
        response = client.post(api_host, json=code).json()
        page_results = response.get("results", [])

        # Teste si une erreur 503 arrive et arrête la boucle si tel est le cas
        if response.get("error") == 503:
            print(response)
            break

        # Affiche une requête toutes les 10 pour du contrôle 
        if page_number % 10 == 0: 
            print(response)

        # Ajouter les résultats de la page courante
        all_results.extend(page_results)

        # Sauvegarder les résultats toutes les 20 pages ou à la dernière page
        if page_number % 20 == 0 or page_number == total_pages:
            print(f"Ajout des pages jusqu'à la page {page_number} dans {file_name}...")
            save_results_to_file(all_results, file_name, page_number)

            # Réinitialiser la liste des résultats sauvegardés
            all_results = []

    print(f"Récupération terminée. Dernière page sauvegardée : {total_pages}")
    return total_pages


In [9]:
code_api_LODA_1 = {
    "recherche": {
        "filtres": [{"dates": {"start": "2008-01-01", "end": "2022-08-31"}, "facette": "DATE_SIGNATURE"}],
        "sort": "SIGNATURE_DATE_DESC",
        "fromAdvancedRecherche": True,
        "champs": [
            {
                "typeChamp": "ALL",
                "criteres": [
                    {"typeRecherche": "UN_DES_MOTS", "valeur": mot, "operateur": "OU"} for mot in [
                        "délinquance", "crime", "délit", "Homicides", "Vols", "Stupéfiants", "Escroquerie",
                        "Contrefaçon", "Sequestrations", "Recels", "Proxénétisme", "Menaces", "Cambriolages",
                        "infraction", "Attentats", "dégradations", "Outrages"
                    ]
                ],
                "operateur": "OU"
            }
        ],
        "pageSize": 100,
        "pageNumber": 1,
        "operateur": "ET",
        "typePagination": "DEFAUT"
    },
    "fond": "LODA_DATE"
}


In [20]:
code_api_LODA_2 = {
    "recherche": {
        "filtres": [{"dates": {"start": "1996-01-01", "end": "1999-12-31"}, "facette": "DATE_SIGNATURE"}],
        "sort": "SIGNATURE_DATE_DESC",
        "fromAdvancedRecherche": True,
        "champs": [
            {
                "typeChamp": "ALL",
                "criteres": [
                    {"typeRecherche": "UN_DES_MOTS", "valeur": mot, "operateur": "OU"} for mot in [
                        "délinquance", "crime", "délit", "Homicides", "Vols", "Stupéfiants", "Escroquerie",
                        "Contrefaçon", "Sequestrations", "Recels", "Proxénétisme", "Menaces", "Cambriolages",
                        "infraction", "Attentats", "dégradations", "Outrages"
                    ]
                ],
                "operateur": "OU"
            }
        ],
        "pageSize": 100,
        "pageNumber": 1,
        "operateur": "ET",
        "typePagination": "DEFAUT"
    },
    "fond": "LODA_DATE"
}

In [11]:
code_api = {
    "recherche": {
        "champs": [
            {
                "typeChamp": "ALL",
                "criteres": [
                    {"typeRecherche": "UN_DES_MOTS", "valeur": mot, "operateur": "OU"} for mot in [
                        "délinquance", "crime", "délit", "Homicides", "Vols", "Stupéfiants", "Escroquerie",
                        "Contrefaçon", "Sequestrations", "Recels", "Proxénétisme", "Menaces", "Cambriolages",
                        "infraction", "Attentats", "dégradations", "Outrages"
                    ]
                ],
                "operateur": "OU"
            }
        ],
        "pageNumber": 1,
        "pageSize": 1,
        "operateur": "ET",
        "sort": "DATE",
        "typePagination": "DEFAUT"
    },
    "fond": "ALL"
}


In [15]:
results_1996_to_2008 = collect_all_results(API_HOST+"/search", code_api_LODA_2, "results_1996_to_2008.json")
results_2008_to_2022 = collect_all_results(API_HOST+"/search", code_api_LODA_1, "results_2008_to_2022.json")

Fichier results_1996_to_2008.json introuvable ou mal structuré. Démarrage depuis la première page.
Total de résultats : 6420
Nombre de pages à récupérer : 65
Reprise à partir de la page 1
Récupération de la page 1/65...
Récupération de la page 2/65...
Récupération de la page 3/65...
Récupération de la page 4/65...
Récupération de la page 5/65...
Récupération de la page 6/65...
Récupération de la page 7/65...
Récupération de la page 8/65...
Récupération de la page 9/65...
Récupération de la page 10/65...
{'executionTime': 7649, 'results': [{'titles': [{'id': 'LEGITEXT000022662845_31-10-2007', 'cid': 'JORFTEXT000000652771', 'title': "Arrêté du 5 octobre 2007 fixant les modalités d'organisation du concours externe et du concours interne de recrutement des conservateurs stagiaires, élèves de l'Ecole nationale supérieure des sciences de l'information et des bibliothèques", 'legalStatus': None, 'startDate': None, 'endDate': None, 'nature': None}], 'text': None, 'type': '_doc', 'nature': 'ARR

In [21]:
results_test = collect_all_results(API_HOST+"/search", code_api_LODA_2, "results_test.json")

Fichier results_test.json introuvable ou mal structuré. Démarrage depuis la première page.
Total de résultats : 1362
Nombre de pages à récupérer : 14
Reprise à partir de la page 1
Récupération de la page 1/14...
Récupération de la page 2/14...
Récupération de la page 3/14...
Récupération de la page 4/14...
Récupération de la page 5/14...
Récupération de la page 6/14...
Récupération de la page 7/14...
Récupération de la page 8/14...
Récupération de la page 9/14...
Récupération de la page 10/14...
{'executionTime': 7237, 'results': [{'titles': [{'id': 'LEGITEXT000005623770_04-05-2002', 'cid': 'JORFTEXT000000200996', 'title': 'Décret n°97-608 du 31 mai 1997 relatif à la formation professionnelle initiale et continue des conducteurs salariés du transport routier public de marchandises', 'legalStatus': None, 'startDate': None, 'endDate': None, 'nature': None}], 'text': None, 'type': '_doc', 'nature': 'DECRET', 'origin': 'LEGI', 'etat': 'VIGUEUR', 'date': '1997-06-01T00:00:00.000+0000', 'sec

Pour pour envoyer des requêtes à l'API nous devons d'abord obtenir un token, après s'être inscrit sur le [site de PISTE](https://piste.gouv.fr/). Ce token est obtenu en envoyant une requête contenant mon identifiant client et mon code de client au site d'autorisation. Nous avons ensuite une autorisation d'une heure avec ce token pour exploiter l'API de Légifrance. 

Maintenant en utilisant le lien d'exploitation de l'API auquel on rajoute l'endpoints qui permet d'accéder à ce que l'on veut faire nous récupérons les données. La liste des endpoints pour l'API de Légifrance est disponible [ici](https://piste.gouv.fr/index.php?option=com_apiportal&view=apitester&usage=api&apitab=tests&apiName=L%C3%A9gifrance&apiId=7e5a0e1d-ffcc-40be-a405-a1a5c1afe950&managerId=3&type=rest&apiVersion=2.4.2&Itemid=179&swaggerVersion=2.0&lang=fr).

Le code ci-dessous permet de récupérer un ensemble de documents appartenant à l'ensemble des lois, ordonnance, décrets et arrêtés de Légifrance entre le premier janvier 1996 et le 31 août 2022 qui contiennent au moins un des mots d'une liste définie. Cette liste comprend les termes des taux de délinquances détaillés [ici](database_délinquance.ipynb#Calcul-des-taux-de-délinquance). Ce code est un json et sera envoyé par une méthode post à l'API, elle nous renverra un nombre de résultats limités (100 ici). Ce code est très inspiré de celui disponible sur le [site de l'API](https://piste.gouv.fr/index.php?option=com_apiportal&view=apitester&usage=api&apitab=tests&apiName=L%C3%A9gifrance&apiId=7e5a0e1d-ffcc-40be-a405-a1a5c1afe950&managerId=3&type=rest&apiVersion=2.4.2&Itemid=179&swaggerVersion=2.0&lang=fr) à l'endpoint /search.

On définit une fonction qui nous permet de récupérer tous les documents de notre recherche, car chaque recherche est limitée à une page de 100 éléments.

In [28]:
def extract_date_from_title(title):
    """
    Extrait la date d'un titre. Si plusieurs dates sont présentes, retourne la plus récente.

    :param title: Le titre de l'objet.
    :return: La date extraite ou None si aucune date valide n'est trouvée.
    """
    # Regex pour les formats de date
    date_patterns = [
        r"(\d{1,2})\s+(janvier|février|mars|avril|mai|juin|juillet|août|septembre|octobre|novembre|décembre)\s+(\d{4})",
        r"(\d{1,2}/\d{1,2}/\d{4})"
    ]

    found_dates = []

    for pattern in date_patterns:
        matches = re.findall(pattern, title, re.IGNORECASE)
        for match in matches:
            if len(match) == 3:  # Format "11 mai 2005"
                day, month, year = match
                month_mapping = {
                    "janvier": 1, "février": 2, "mars": 3, "avril": 4, "mai": 5, "juin": 6,
                    "juillet": 7, "août": 8, "septembre": 9, "octobre": 10, "novembre": 11, "décembre": 12
                }
                month_num = month_mapping[month.lower()]
                found_dates.append(datetime(int(year), month_num, int(day)))
            elif len(match) == 1:  # Format "12/12/2014"
                date_str = match[0]
                found_dates.append(datetime.strptime(date_str, "%d/%m/%Y"))

    if found_dates:
        return max(found_dates).strftime("%Y-%m-%d")  # Retourne la date la plus récente au format AAAA-MM-JJ

    return None

In [29]:
def results_to_dataframe(json_data):
    """
    Convertit les données JSON en DataFrame en extrayant des champs spécifiques.

    :param json_data: Les données JSON à analyser.
    :return: Un DataFrame contenant les données extraites.
    """
    data = []

    # Accéder à la liste des résultats
    results = json_data.get("results", [])

    for result in results:
        # Extraire les informations requises
        titles = result.get("titles")
        title_info = titles[0] if isinstance(titles, list) and titles else {}

        title = title_info.get("title")
        id = title_info.get("id")
        date = extract_date_from_title(title)  # Extraire uniquement à partir du titre
        nature = result.get("nature")
        etat = result.get("etat")
        origin = result.get("origin")
        date_publication = result.get("datePublication")

        # Ajouter les données dans la liste
        data.append({
            "Titre": title,
            "ID": id,
            "Date": date,
            "Nature": nature,
            "Etat": etat,
            "Origine": origin,
            "Date Publication": date_publication
        })

    # Créer et retourner un DataFrame
    return pd.DataFrame(data)


In [ ]:
with open("results_LODA.json", "r", encoding="utf-8") as file:
    json_data = json.load(file)
df_LODA = results_to_dataframe(json_data)

In [ ]:
df_LODA = df_LODA.drop_duplicates()
df_LODA.to_csv("resultats_legifrance_loda.csv", index=False)